In [1]:
# Carregando
#começa tratando os dados e limpa a base
import pandas as pd
import numpy as np
import csv

dados = pd.read_csv('dados.csv', sep=';', encoding='utf-8', decimal=',')
#dados.head(5)




In [2]:
#dados.dtypes
# selecao do periodo de analise 

dados['DATA'] = pd.to_datetime(dados['DATA'], format='%d/%m/%Y')

df_merged =pd.DataFrame()


ano = list([2010,2011,2012,2013,2014,2015,2016,2017,2018,2019,2020])


for x in ano:
    selecao = (dados['DATA'] >=str(x)+'/09/01') & (dados['DATA'] <=  str(x+1)+'/04/30')
    
    df_filtrado = dados[selecao]


    df_merged = pd.concat([df_merged, df_filtrado], ignore_index=True) 




In [ ]:
from datetime import datetime
#inicio da estacao chuvosa 

nome_estacao='DIAMANTINA'
    
inciochuva = df_merged.loc[:,['DATA', nome_estacao] ]
final_chuva=[]

marcador_inicio=False
ano_do_incio_chuva=0
marcador_final=False

somador_ml=0
somador_ml_final_chuva=0

for index, row in inciochuva.iterrows():
    leitura_chuva= row[nome_estacao]     
    
    if leitura_chuva>=0:
        somador_ml= somador_ml+leitura_chuva;

    if somador_ml>=10 and not marcador_inicio:
        marcador_inicio=True
        data_incio_chuva= row['DATA'] 
        ano_atual= row['DATA'].year
        print ('estacao:', nome_estacao,'INCIO:', data_incio_chuva, 'MM', somador_ml)
        somador_ml=0
        ano_do_incio_chuva= ano_atual
        marcador_final=False
        #print ('estacao:',ano_do_incio_chuva)

final_chuva =  inciochuva[::-1] 
print ('ano incio chuva:',ano_do_incio_chuva)
for index, row in final_chuva.iterrows():     
    leitura_chuva= row[nome_estacao] 
    ano_atual= int(row['DATA'].year)
    data_atual= row['DATA'] 
    
    if leitura_chuva>=0 and data_atual <= datetime.strptime(str(ano_do_incio_chuva+1)+'-04-30', '%Y-%m-%d') :
        somador_ml_final_chuva = somador_ml_final_chuva +leitura_chuva

    if somador_ml_final_chuva>=5  and not marcador_final: 
        marcador_final=True       
        data_final_chuva=  row['DATA'] 
        print ('estacao:', nome_estacao,'FINAL:', data_final_chuva, 'MM', somador_ml_final_chuva)
        somador_ml_final_chuva=0
        marcador_inicio=False
        print ('ano final chuva:', ano_do_incio_chuva+1)
        


In [3]:
import csv
from datetime import datetime

with open('iniciofimestacao.csv', 'w') as file:
    cabecalho = ['estacao', 'inicio','final']
    writer = csv.DictWriter(file, fieldnames=cabecalho,delimiter=';')
    writer.writeheader() # Escreve o cabeçalho


#inicio da estacao chuvosa 
ano = list([2010,2011,2012,2013,2014,2015,2016,2017,2018,2019,2020])

#extrair nome coulas e remove a data
estacao= list(dados.columns)
estacao.pop(0)



for xrow in estacao: #percorre a lista das estacoes

    for x in ano: # de cada estacao percorre o ano

        selecao = (dados['DATA'] >=str(x)+'/09/01') & (dados['DATA'] <=  str(x+1)+'/04/30')    
        df_filtrado_ano = dados[selecao]   

        nome_estacao=xrow
        inciochuva = df_filtrado_ano.loc[:,['DATA', nome_estacao] ]
        final_chuva=[]

        marcador_inicio=False
        ano_do_incio_chuva=0
        marcador_final=False

        somador_ml=0
        somador_ml_final_chuva=0

        for index, row in inciochuva.iterrows():
            leitura_chuva= row[nome_estacao]     
    
            if leitura_chuva>=0:
                somador_ml= somador_ml+leitura_chuva;

            if somador_ml>=10 and not marcador_inicio:
                marcador_inicio=True
                data_incio_chuva= row['DATA'] 
                ano_atual= row['DATA'].year
                #print ('estacao:', nome_estacao,'INCIO:', data_incio_chuva, 'MM', somador_ml)
                dtinicio=data_incio_chuva
                somador_ml=0
                ano_do_incio_chuva= ano_atual
                marcador_final=False
                #print ('estacao:',ano_do_incio_chuva)

        
        final_chuva =  inciochuva[::-1] 
        
        for index, row in final_chuva.iterrows():     
            leitura_chuva= row[nome_estacao] 
            ano_atual= int(row['DATA'].year)
            data_atual= row['DATA'] 
    
            if leitura_chuva>=0 and data_atual <= datetime.strptime(str(ano_do_incio_chuva+1)+'-04-30', '%Y-%m-%d') :
                somador_ml_final_chuva = somador_ml_final_chuva +leitura_chuva

            if somador_ml_final_chuva>=5  and not marcador_final: 
                marcador_final=True       
                data_final_chuva=  row['DATA'] 
                #print ('estacao:', nome_estacao,'FINAL:', data_final_chuva, 'MM', somador_ml_final_chuva)
                dtfinal = data_final_chuva
                somador_ml_final_chuva=0
                marcador_inicio=False
            #print ('ano final chuva:', ano_do_incio_chuva+1)
        
        #print ('estacao:', nome_estacao,'INCIO:', data_incio_chuva,'FINAL:', data_final_chuva )
        with open('iniciofimestacao.csv', 'a') as file:
            writer = csv.DictWriter(file, fieldnames=cabecalho, delimiter=';')                    
            writer.writerow({'estacao':nome_estacao, 'inicio':data_incio_chuva,'final':data_final_chuva})    




In [ ]:
#extrair nome coulas e remove a data
estacao= list(dados.columns)
estacao.pop(0)


In [4]:
with open('final.csv', 'w') as file:
    cabecalho = ['estacao', 'inicio','final', 'qtdias']
    writer = csv.DictWriter(file, fieldnames=cabecalho, delimiter=';')
    writer.writeheader() # Escreve o cabeçalho

marcador_inicio= False
marcador_final= False
marcador_primeirodia= False
leitura_chuva=0
cont_veranico=0
data_anterior=''
data_incio=''


for xrow in estacao: #percorre a lista das estacoes

    nome_estacao=xrow
    
    novo = dados.loc[:,['DATA', nome_estacao] ]
    novo[nome_estacao] = novo[nome_estacao].astype(float)

    for index, row in novo.iterrows():
        leitura_chuva= row[nome_estacao] 
        data= row['DATA']
        if (marcador_inicio):
            if leitura_chuva <=0:
                cont_veranico= cont_veranico+1
            else:
                marcador_final= True
        
        if (cont_veranico==1 and marcador_inicio):
            data_incio= data           
        if marcador_final:
            if (cont_veranico>=4):
                
                #print ('estacao:', nome_estacao,'INCIO:', data_incio, '  FIM:', data_anterior , '   DIAS:',  cont_veranico) 
                with open('final.csv', 'a') as file:
                    writer = csv.DictWriter(file, fieldnames=cabecalho, delimiter=';')                    
                    writer.writerow({'estacao':nome_estacao, 'inicio':data_incio,'final':data_anterior, 'qtdias':cont_veranico})               




    #toda ver que chove mais que 0.5 mm ele reinicia o contador
        if leitura_chuva >0:       
            marcador_inicio= True
            cont_veranico= 0
            marcador_final= False

        data_anterior= data
        
